# Grabbing Wave Heights from the COAWST forecast

Based on Rich Signell (rsignell-usgs) COAWST Explorer notebook     
https://github.com/reproducible-notebooks/Holoviz-Demos/blob/master/COAWST-Explorer.ipynb

In [15]:
import xarray as xr
import cf_xarray 
import intake
import numpy as np

Above and beyond the Pangeo environment, I needed to install cf_xarray, intake, s3fs, intake-xarray

In [24]:
url = 'https://mghp.osn.xsede.org/rsignellbucket1/catalogs/ioos_intake_catalog.yml'

In [25]:
url

'https://mghp.osn.xsede.org/rsignellbucket1/catalogs/ioos_intake_catalog.yml'

In [26]:
cat = intake.open_catalog(url)
list(cat)

['COAWST-Archive', 'LiveOcean-Archive']

In [27]:
cat

ioos_intake_catalog:
  args:
    path: https://mghp.osn.xsede.org/rsignellbucket1/catalogs/ioos_intake_catalog.yml
  description: ''
  driver: intake.catalog.local.YAMLFileCatalog
  metadata: {}


In [28]:
cat['COAWST-Archive']

COAWST-Archive:
  args:
    consolidated: false
    storage_options:
      fo: s3://rsignellbucket1/COAWST/archive.json
      remote_options:
        anon: true
        client_kwargs:
          endpoint_url: https://mghp.osn.xsede.org
      remote_protocol: s3
      target_options:
        anon: true
        client_kwargs:
          endpoint_url: https://mghp.osn.xsede.org
    urlpath: reference://
  description: COAWST Forecast Archive
  driver: intake_xarray.xzarr.ZarrSource
  metadata:
    catalog_dir: https://mghp.osn.xsede.org/rsignellbucket1/catalogs


In [29]:
ds = cat['COAWST-Archive'].to_dask()

In [30]:
time_vars = []
for var in ds.data_vars:
    if len(ds[var].dims) > 0:
        if 'time' in ds[var].dims[0] and not 'bounds' in var:
            time_vars.append(var)

In [31]:
init_var = 'Hwave'

In [32]:
ds

<xarray.Dataset>
Dimensions:                 (ocean_time: 1301, s_w: 17, eta_rho: 336,
                             xi_rho: 896, tracer: 8, s_rho: 16, NST: 6,
                             boundary: 4, Nbed: 1, eta_u: 336, xi_u: 895,
                             eta_v: 335, xi_v: 896, eta_psi: 335, xi_psi: 895)
Coordinates:
    lat_psi                 (eta_psi, xi_psi) float64 dask.array<chunksize=(335, 895), meta=np.ndarray>
    lat_rho                 (eta_rho, xi_rho) float64 dask.array<chunksize=(336, 896), meta=np.ndarray>
    lat_u                   (eta_u, xi_u) float64 dask.array<chunksize=(336, 895), meta=np.ndarray>
    lat_v                   (eta_v, xi_v) float64 dask.array<chunksize=(335, 896), meta=np.ndarray>
    lon_psi                 (eta_psi, xi_psi) float64 dask.array<chunksize=(335, 895), meta=np.ndarray>
    lon_rho                 (eta_rho, xi_rho) float64 dask.array<chunksize=(336, 896), meta=np.ndarray>
    lon_u                   (eta_u, xi_u) float64 dask.array<chunksize=(336, 895), meta=np.ndarray>
    lon_v                   (eta_v, xi_v) float64 dask.array<chunksize=(335, 896), meta=np.ndarray>
  * ocean_time              (ocean_time) datetime64[ns] 2022-07-29T01:00:00 ....
  * s_rho                   (s_rho) float64 -0.9688 -0.9062 ... -0.03125
  * s_w                     (s_w) float64 -1.0 -0.9375 -0.875 ... -0.0625 nan
Dimensions without coordinates: eta_rho, xi_rho, tracer, NST, boundary, Nbed,
                                eta_u, xi_u, eta_v, xi_v, eta_psi, xi_psi
Data variables: (12/187)
    AKs                     (ocean_time, s_w, eta_rho, xi_rho) float32 dask.array<chunksize=(1, 9, 168, 448), meta=np.ndarray>
    AKt                     (ocean_time, s_w, eta_rho, xi_rho) float32 dask.array<chunksize=(1, 9, 168, 448), meta=np.ndarray>
    AKv                     (ocean_time, s_w, eta_rho, xi_rho) float32 dask.array<chunksize=(1, 9, 168, 448), meta=np.ndarray>
    Akk_bak                 (ocean_time) float64 dask.array<chunksize=(1,), meta=np.ndarray>
    Akp_bak                 (ocean_time) float64 dask.array<chunksize=(1,), meta=np.ndarray>
    Akt_bak                 (ocean_time, tracer) float64 dask.array<chunksize=(1, 8), meta=np.ndarray>
    ...                      ...
    wetdry_mask_psi         (ocean_time, eta_psi, xi_psi) float32 dask.array<chunksize=(1, 335, 895), meta=np.ndarray>
    wetdry_mask_rho         (ocean_time, eta_rho, xi_rho) float32 dask.array<chunksize=(1, 336, 896), meta=np.ndarray>
    wetdry_mask_u           (ocean_time, eta_u, xi_u) float32 dask.array<chunksize=(1, 336, 895), meta=np.ndarray>
    wetdry_mask_v           (ocean_time, eta_v, xi_v) float32 dask.array<chunksize=(1, 335, 896), meta=np.ndarray>
    xl                      (ocean_time) float64 dask.array<chunksize=(1,), meta=np.ndarray>
    zeta                    (ocean_time, eta_rho, xi_rho) float32 dask.array<chunksize=(1, 336, 896), meta=np.ndarray>
Attributes: (12/37)
    CPP_options:       COAWST, ANA_BPFLUX, ANA_BSFLUX, ANA_BTFLUX, ANA_FSOBC,...
    Conventions:       CF-1.4, SGRID-0.3
    NLM_LBC:           \nEDGE:         WEST   SOUTH  EAST   NORTH  \nzeta:   ...
    ana_file:          ROMS/Functionals/ana_btflux.h, ROMS/Functionals/ana_fs...
    bry_file_01:       ./forcings3/USE_coawst_bdy.nc
    clm_file_01:       ./forcings3/USE_coawst_clm.nc
    ...                ...
    svn_url:           
    tide_file:         ../forcings/tide_forc_USeast_grd16_osu_rev2.nc
    tiling:            006x004
    title:             COAWST ROMS SWAN
    type:              ROMS/TOMS history file
    var_info:          ROMS/External/varinfo.dat

In [33]:
import hvplot.xarray
from geoviews import tile_sources as gvts
import panel as pn

In [34]:
var_select = pn.widgets.Select(name='COAWST Variables:', options=time_vars, 
                               value=init_var)

In [35]:
base_map_select = pn.widgets.Select(name='Basemap:', options=gvts.tile_sources, value=gvts.OSM)


In [36]:
da = ds[init_var].cf.isel(T=slice(-40,-1)).unify_chunks()


In [37]:
len(da.shape)

3

In [42]:
time_vals = 60


In [43]:
@pn.depends(var_select, base_map_select)
def plot(var, base_map):
    extra_dims = list(ds[var].dims[:-2])
    da = ds[var].cf.isel(T=slice(-time_vals,-1)).unify_chunks()
    if len(da.shape) == 4:
        mesh = da.hvplot.quadmesh(x=da.cf['longitude'].name, y=da.cf['latitude'].name, 
                              rasterize=True, geo=True, title=var, attr_labels=False, 
                              fields={da.cf['Z'].name: {'default': float(da.cf['Z'].values[-1])}},
                              groupby=extra_dims, cmap='turbo', width=600, grid=True,
                              height=600).opts(alpha=0.7, data_aspect=None, active_tools=['wheel_zoom', 'pan'])
    else:
        mesh = da.hvplot.quadmesh(x=da.cf['longitude'].name, y=da.cf['latitude'].name, 
                              rasterize=True, geo=True, title=var, attr_labels=False, 
                              groupby=extra_dims, cmap='turbo', width=600, grid=True,
                              height=600).opts(alpha=0.7, data_aspect=None, active_tools=['wheel_zoom', 'pan'])
    return pn.panel(mesh * base_map, widgets={k: pn.widgets.Select for k in extra_dims})

In [44]:
col = pn.Column(var_select, base_map_select, plot)


In [45]:
col.servable('COAWST Dashboard')

Column
    [0] Select(name='COAWST Variables:', options=['AKs', 'AKt', ...], value='Uwind')
    [1] Select(name='Basemap:', options={'CartoDark': :WMTS   [Lon...}, value=WMTS)
    [2] ParamFunction(function)